In [402]:
import os
import matplotlib.pyplot as plt
import numpy as np
plt.ioff();
try:
    maindir
except NameError:
    maindir = os.path.dirname(os.getcwd())
for module in os.listdir(maindir + '\\testing_modules'):
    %run -i "{maindir}\\testing_modules\\{module}"
base = os.path.dirname(os.path.dirname(maindir)) + '\\'
plt.ion();
np.set_printoptions(suppress=True)

In [403]:
%matplotlib qt
import matplotlib
import skimage.io as io
from skimage.restoration import rolling_ball
from pyFAI.azimuthalIntegrator import AzimuthalIntegrator
from pyFAI.calibrant import Calibrant
from pyFAI.geometryRefinement import GeometryRefinement
from skimage.feature import peak_local_max
from pyFAI.detectors._others import Dexela2923, Fairchild, Pixium

In [404]:
filedir = '''D:\\Musterman_postdoc\\20231030_Musterman\\'''
if not os.path.exists(filedir):
    filedir = '''C:\\Users\\emusterma\\OneDrive - Brookhaven National Laboratory\\Documents\\Postdoc\\Data\\20231030\\'''
calibrant_filename = '''scan149218_dexela_calibration.tif'''
energy = 18
wavelength = energy_2_wavelength(energy) * 1e-10

calibrant_img = io.imread(filedir + calibrant_filename).astype(np.float32)
dexela_dark = io.imread('''C:\\Users\\emusterma\\OneDrive - Brookhaven National Laboratory\\Documents\\Postdoc\\DOE_SCGSR\\Data Analysis\\After 2nd beamtime\\dexela_df_avg.tif''').astype(np.float32)
dexela_mask = np.ones((calibrant_img.shape))
dexela_mask[-1] = 9
bkg_img = rolling_ball(calibrant_img, radius=15)
fixed_img = calibrant_img / dexela_mask - bkg_img - 0.125 * dexela_dark

In [405]:
fig, ax = plt.subplots(1, 1, figsize=(6, 5), dpi=200)

#im = ax.imshow(calibrant_img - 0.25 * dexela_dark, norm=matplotlib.colors.LogNorm())
im = ax.imshow(fixed_img)
fig.colorbar(im, ax=ax)

plt.show()

In [407]:
thresh = 0.5e3
proc_img = gaussian_filter(median_filter(fixed_img, size=(1, 1)), sigma=(1, 1))
#proc_img = gaussian_filter(median_filter(fixed_img, size=(1, 1)), sigma=(0.5, 0.5))
proc_img[proc_img < thresh] = np.nan
proc_img[~np.isnan(proc_img)] = 1

temp_image = np.copy(proc_img)
temp_image[np.isnan(proc_img)] = 0
blob_img = expand_labels(temp_image, distance=1)

blob_img = label(blob_img).astype(np.float32)
blob_labels = np.unique(blob_img)

for blob in blob_labels:
    if (blob not in blob_img[0:1] or blob not in blob_img[-2:-1]):
        if ((np.any((blob_img[:, 0] == blob) & (blob_img[::-1, 0] == blob))
            or np.any((blob_img[:, -1] == blob) & (blob_img[::-1, -1] == blob)))):
            print('one survived')
            continue
        else:
            print(f'removing label {blob}')
            #blob_img[blob_img == blob] = 0

blob_img = label(blob_img.T).astype(np.float32).T

fig, ax = plt.subplots(1, 1, figsize=(6, 5), dpi=200)

im = ax.imshow(blob_img)
fig.colorbar(im, ax=ax)

plt.show()

removing label 8.0
removing label 9.0
removing label 11.0
removing label 13.0
removing label 14.0
removing label 15.0
removing label 16.0
removing label 17.0
removing label 18.0
removing label 19.0
one survived
removing label 21.0
removing label 22.0
removing label 23.0
removing label 24.0
removing label 25.0
removing label 26.0
removing label 27.0
removing label 28.0
removing label 29.0
removing label 30.0
removing label 31.0
removing label 32.0
removing label 33.0
removing label 34.0
removing label 35.0
removing label 36.0
removing label 37.0
removing label 38.0
removing label 39.0
removing label 40.0
removing label 41.0
removing label 42.0
removing label 43.0
removing label 44.0
removing label 45.0
removing label 46.0
removing label 47.0
removing label 48.0
removing label 49.0
removing label 50.0
removing label 51.0
removing label 52.0
removing label 53.0
removing label 54.0


In [27]:
spots = peak_local_max(fixed_img, threshold_rel=0.0001)
print(len(spots))

fig, ax = plt.subplots(1, 1, figsize=(6, 5), dpi=200)

im = ax.imshow(fixed_img)
ax.scatter(*spots.T[::-1], c='r', s=1)
fig.colorbar(im, ax=ax)

plt.show()

3200


In [33]:
x_lst, y_lst, ring_lst = [], [], []
for spot in spots:
    if int(blob_img[*spot]) != 0:
        #x_lst.append(486 - spot[0])
        x_lst.append(spot[0])
        y_lst.append(spot[1])
        ring_lst.append(int(blob_img[*spot]) - 1)

data = np.array([x_lst, y_lst, ring_lst]).T
print(len(data))

fig, ax = plt.subplots(1, 1, figsize=(6, 5), dpi=200)

im = ax.imshow(fixed_img)
ax.scatter(data[:, 1], data[:, 0], c=data[:, 2], s=1)
fig.colorbar(im, ax=ax)

plt.show()
new_spots = data[:, :-1]

3158


In [33]:
reference_file = '''C:\\Users\\emusterma\\OneDrive - Brookhaven National Laboratory\\Documents\\Postdoc\\DOE_SCGSR\\Data\\221128 Beamtime\\maps\\zincite_extended.txt'''
calibrant = Calibrant(filename=reference_file, wavelength=wavelength)
dexela2315 = Dexela2315()
dexela2315.set_binning(bin_size=(4, 4))

#tr = GeometryRefinement(data=data, detector=dexela2315, calibrant=calibrant, wavelength=energy_2_wavelength(18)*1e-10,
#                                                dist=0.425, poni1=0.07, poni2=0.16, rot1=0.54, rot2=0, rot3=0)
tr = GeometryRefinement(data=data, detector=dexela2315, calibrant=calibrant, wavelength=wavelength)

In [34]:
print(tr.param, tr.energy)

[0.21713423606178558, 0.06912313131536871, 0.1719973269265199, 0.6891260297723616, 0.010974966747997314, 0.0] 14.999999999999998


In [35]:
tr.refine3(fix='wavelength') # ALWAYS fix wavelength. Refinement yields distances and energy otherwise

0.00044931509613461046

In [36]:
print(tr.param, tr.energy)

[0.36015035216298746, 0.07750011184365128, -0.0005245886019737451, 0.1799899634142498, -0.009077382334506362, -1.8221972238451893e-06] 14.999999999999998


In [37]:
res = tr.integrate2d_ng(fixed_img, 1024, 360, unit='2th_deg')
tth, chi = res[1], res[2]

In [38]:
fig, ax = plt.subplots(2, 1, figsize=(10, 5), dpi=200, sharex=True)

res = tr.integrate2d_ng(fixed_img, 4096, 360, unit='2th_deg')
tth, chi = res[1], res[2]

im = ax[0].imshow(res[0], extent=[tth[0], tth[-1], chi[0], chi[-1]], vmin=0, aspect='auto')
fig.colorbar(im, ax=ax)
ax[0].set_xlabel('Scattering Angle, 2θ [°]')
ax[0].set_ylabel('Azimuthal Angle, χ [°]')

ax[1].plot(*tr.integrate1d_ng(fixed_img, 4096, unit='2th_deg'))


plt.show()

In [54]:
import numpy as np
import matplotlib.pyplot as plt

def cartesian_ellipse(xy, a, b, c, d, e, f):
    x = xy[0]
    y = xy[1]

    return 


def fit_ellipse(x, y):
    """

    Fit the coefficients a,b,c,d,e,f, representing an ellipse described by
    the formula F(x,y) = ax^2 + bxy + cy^2 + dx + ey + f = 0 to the provided
    arrays of data points x=[x1, x2, ..., xn] and y=[y1, y2, ..., yn].

    Based on the algorithm of Halir and Flusser, "Numerically stable direct
    least squares fitting of ellipses'.


    """

    D1 = np.vstack([x**2, x * y, y**2]).T
    D2 = np.vstack([x, y, np.ones(len(x))]).T
    S1 = D1.T @ D1
    S2 = D1.T @ D2
    S3 = D2.T @ D2
    T = -np.linalg.inv(S3) @ S2.T
    M = S1 + S2 @ T
    C = np.array(((0, 0, 2), (0, -1, 0), (2, 0, 0)), dtype=float)
    M = np.linalg.inv(C) @ M
    eigval, eigvec = np.linalg.eig(M)
    con = 4 * eigvec[0]* eigvec[2] - eigvec[1]**2
    ak = eigvec[:, np.nonzero(con > 0)[0]]
    return np.concatenate((ak, T @ ak)).ravel()


def cart_to_pol(coeffs):
    """

    Convert the cartesian conic coefficients, (a, b, c, d, e, f), to the
    ellipse parameters, where F(x, y) = ax^2 + bxy + cy^2 + dx + ey + f = 0.
    The returned parameters are x0, y0, ap, bp, e, phi, where (x0, y0) is the
    ellipse centre; (ap, bp) are the semi-major and semi-minor axes,
    respectively; e is the eccentricity; and phi is the rotation of the semi-
    major axis from the x-axis.

    """

    # We use the formulas from https://mathworld.wolfram.com/Ellipse.html
    # which assumes a cartesian form ax^2 + 2bxy + cy^2 + 2dx + 2fy + g = 0.
    # Therefore, rename and scale b, d and f appropriately.
    a = coeffs[0]
    b = coeffs[1] / 2
    c = coeffs[2]
    d = coeffs[3] / 2
    f = coeffs[4] / 2
    g = coeffs[5]

    den = b**2 - a*c
    if den > 0:
        raise ValueError('coeffs do not represent an ellipse: b^2 - 4ac must'
                         ' be negative!')

    # The location of the ellipse centre.
    x0, y0 = (c*d - b*f) / den, (a*f - b*d) / den

    num = 2 * (a*f**2 + c*d**2 + g*b**2 - 2*b*d*f - a*c*g)
    fac = np.sqrt((a - c)**2 + 4*b**2)
    # The semi-major and semi-minor axis lengths (these are not sorted).
    ap = np.sqrt(num / den / (fac - a - c))
    bp = np.sqrt(num / den / (-fac - a - c))

    # Sort the semi-major and semi-minor axis lengths but keep track of
    # the original relative magnitudes of width and height.
    width_gt_height = True
    if ap < bp:
        width_gt_height = False
        ap, bp = bp, ap

    # The eccentricity.
    r = (bp/ap)**2
    if r > 1:
        r = 1/r
    e = np.sqrt(1 - r)

    # The angle of anticlockwise rotation of the major-axis from x-axis.
    if b == 0:
        phi = 0 if a < c else np.pi/2
    else:
        phi = np.arctan((2.*b) / (a - c)) / 2
        if a > c:
            phi += np.pi/2
    if not width_gt_height:
        # Ensure that phi is the angle to rotate to the semi-major axis.
        phi += np.pi/2
    phi = phi % np.pi

    return x0, y0, ap, bp, e, phi


def get_ellipse_pts(params, npts=100, tmin=0, tmax=2*np.pi):
    """
    Return npts points on the ellipse described by the params = x0, y0, ap,
    bp, e, phi for values of the parametric variable t between tmin and tmax.

    """

    x0, y0, ap, bp, e, phi = params
    # A grid of the parametric variable, t.
    t = np.linspace(tmin, tmax, npts)
    x = x0 + ap * np.cos(t) * np.cos(phi) - bp * np.sin(t) * np.sin(phi)
    y = y0 + ap * np.cos(t) * np.sin(phi) + bp * np.sin(t) * np.cos(phi)
    return x, y


if __name__ == '__main__':
    # Test the algorithm with an example elliptical arc.
    npts = 250
    tmin, tmax = np.pi/6, 4 * np.pi/3
    x0, y0 = 4, -3.5
    ap, bp = 7, 3
    phi = np.pi / 4
    # Get some points on the ellipse (no need to specify the eccentricity).
    x, y = get_ellipse_pts((x0, y0, ap, bp, None, phi), npts, tmin, tmax)
    noise = 0.1
    x += noise * np.random.normal(size=npts) 
    y += noise * np.random.normal(size=npts)

    coeffs = fit_ellipse(x, y)
    print('Exact parameters:')
    print('x0, y0, ap, bp, phi =', x0, y0, ap, bp, phi)
    print('Fitted parameters:')
    print('a, b, c, d, e, f =', coeffs)
    x0, y0, ap, bp, e, phi = cart_to_pol(coeffs)
    print('x0, y0, ap, bp, e, phi = ', x0, y0, ap, bp, e, phi)

    plt.plot(x, y, 'x')     # given points
    x, y = get_ellipse_pts((x0, y0, ap, bp, e, phi))
    plt.plot(x, y)
    plt.show()


Exact parameters:
x0, y0, ap, bp, phi = 4 -3.5 7 3 0.7853981633974483
Fitted parameters:
a, b, c, d, e, f = [ -0.51733144   0.69491003  -0.49946794   6.48425125  -6.25240455
 -16.0905626 ]
x0, y0, ap, bp, e, phi =  3.872598607926932 -3.565090583511025 6.8787781952515274 2.9817110201407613 0.9011703022103111 0.7982484342121114


In [78]:
fig, ax = plt.subplots(1, 1, figsize=(10, 5), dpi=200)

mask = data[:, 2] == 13
x0, y0, ap, bp, e, phi = cart_to_pol(fit_ellipse(data[:, 1][mask], data[:, 0][mask]))
x, y = get_ellipse_pts((x0, y0, ap, bp, e, phi))

im = ax.imshow(fixed_img)
fig.colorbar(im, ax=ax)
ax.scatter(data[:, 1][mask], data[:, 0][mask], c='r', s=1)

ax.plot(x, y)

plt.show()

In [ ]:
def fit_concentric_rings():

    

    def polar_ellispe_1d(chi, a, e, phi):
    # chi is the azimuthal angle
    # a is the major axis length
    # e is the eccentricity
    # phi is the rotation angle...I think...
    return a * (1 - (e ** 2)) / (1 - e * np.cos(chi - phi))

In [136]:
list(range(5))

[0, 1, 2, 3, 4]

In [249]:
from sklearn.metrics.pairwise import euclidean_distances
spots = peak_local_max(fixed_img, threshold_rel=0.001)
dist = euclidean_distances(spots)

spot_indices = list(range(len(spots)))
max_dist = 50
max_neighbors = 3

dist[dist > max_dist] = np.nan
dist[dist == 0] = np.nan

data = np.empty((len(spots), 3))
data[:] = np.nan
data[:, :-1] = spots

labels=[0]
for i in spot_indices:
    connections = dist[i] < max_dist
    if sum(connections) > max_neighbors:
        connections = dist[i] <= sorted(dist[i][connections])[max_neighbors - 1]
    if np.all(np.isnan(data[connections][:, -1])):
        for index, con in enumerate(connections):
            if con:
                data[index, -1] = labels[-1]
        labels.append(labels[-1] + 1)
    else:
        base_label = np.nanmin(data[connections][:, -1])
        for index, con in enumerate(connections):
            if con:
                data[index, -1] = base_label

In [396]:
def label_nearest_spots(spots, max_dist=25, max_neighbors=np.inf):
    from sklearn.metrics.pairwise import euclidean_distances
    dist = euclidean_distances(spots)

    spot_indices = list(range(len(spots)))

    # Ignore distances greater than bounds
    # Ignore same pairs
    dist[dist > max_dist] = np.nan
    #dist[dist == 0] = np.nan
    # Create dataset
    data = np.empty((len(spots), 3))
    data[:] = np.nan
    data[:, :-1] = spots

    labels=[0]
    for i in spot_indices:
        # This seems unecessary...
        connections = dist[i] < max_dist

        # Useful for connectivity
        if sum(connections) > max_neighbors:
            connections = dist[i] <= sorted(dist[i][connections])[max_neighbors - 1]
            #break
            
        extra_labels = np.unique(data[connections][:, -1])
        extra_labels = extra_labels[~np.isnan(extra_labels)]

        # Find new label if all points are unlabeled
        if np.all(np.isnan(data[connections][:, -1])):
            current_label = labels[-1] + 1
            data[connections, -1] = current_label
            labels.append(current_label)
            #print('New label added')

        # Otherwise relabel all to lowest label value
        else:
            base_label = np.nanmin(data[connections][:, -1])
            data[connections, -1] = base_label
            current_label = base_label

        
        # Relabel previous labels if connected with others...
        if np.any(extra_labels != current_label):
            for extra in extra_labels:
                if np.all([extra != current_label, 
                        not np.isnan(extra), 
                        extra in labels]):
                    #print('I should be here...')
                    
                    data[[data[:, -1] == extra][0], -1] = current_label
                    labels.remove(extra)

    data = data.astype(np.int32)
    labels = np.array(labels).astype(np.int32)
    # labels is not perfectly sequential. Why???
    return data

In [371]:
# Redo to account for different distance values. Currently using pixel differences
from sklearn.metrics.pairwise import euclidean_distances
dist = euclidean_distances(new_spots)

spot_indices = list(range(len(new_spots)))

# Ignore distances greater than bounds
# Ignore same pairs
max_dist = 10
max_neighbors = 3
dist[dist > max_dist] = np.nan
#dist[dist == 0] = np.nan
# Create dataset
data = np.empty((len(new_spots), 3))
data[:] = np.nan
data[:, :-1] = new_spots

labels=[0]
for i in spot_indices:
    i = np.random.randint(0, np.max(spot_indices))
    # This seems unecessary...
    connections = dist[i] < max_dist

    # Useful for connectivity
    if sum(connections) > max_neighbors:
        connections = dist[i] <= sorted(dist[i][connections])[max_neighbors - 1]
        #break
        
    extra_labels = np.unique(data[connections][:, -1])
    extra_labels = extra_labels[~np.isnan(extra_labels)]
    if len(extra_labels) > 1:
       #break
       pass

    # Find new label if all points are unlabeled
    if np.all(np.isnan(data[connections][:, -1])):
        current_label = labels[-1] + 1
        data[connections, -1] = current_label
        labels.append(current_label)
        #print('New label added')

    # Otherwise relabel all to lowest label value
    else:
        base_label = np.nanmin(data[connections][:, -1])
        data[connections, -1] = base_label
        current_label = base_label

    
    # Relabel previous labels if connected with others...
    if np.any(extra_labels != current_label):
        for extra in extra_labels:
            if np.all([extra != current_label, 
                       not np.isnan(extra), 
                       extra in labels]):
                #print('I should be here...')
                
                data[[data[:, -1] == extra][0], -1] = current_label
                labels.remove(extra)
                #print(f'Relabelled and removed label {extra}.')

    #break

fig, ax = plt.subplots(1, 1, figsize=(10, 5), dpi=200)

im = ax.imshow(fixed_img)
fig.colorbar(im, ax=ax)
ax.scatter(data[:, 1], data[:, 0], c='k', s=1)
ax.scatter(data[:, 1][connections], data[:, 0][connections], c='r', s=1)
ax.scatter(data[i, 1], data[i, 0], marker='*', c='w', s=5)

plt.show()
#data = data.astype(np.int32)
#labels = np.array(labels).astype(np.int32)
# labels is not perfectly sequential. Why???
print(len(np.unique(data[:, -1])))

369


In [361]:
connections

array([False, False, False, ..., False, False, False])

In [342]:
fig, ax = plt.subplots(1, 1, figsize=(10, 5), dpi=200)

im = ax.imshow(fixed_img)
fig.colorbar(im, ax=ax)
ax.scatter(data[:, 1], data[:, 0], c='k', s=1)
ax.scatter(data[:, 1][connections], data[:, 0][connections], c='r', s=1)

plt.show()

In [372]:
fig, ax = plt.subplots(1, 1, figsize=(10, 5), dpi=200)

im = ax.imshow(fixed_img)
fig.colorbar(im, ax=ax)
ax.scatter(data[:, 1], data[:, 0], c=data[:, 2], s=1, cmap='tab20')

plt.show()

In [392]:
dist = euclidean_distances(new_spots)
fig, ax = plt.subplots(1, 1, figsize=(5, 5), dpi=200)
i = np.random.randint(dist.shape[0])

ax.hist(dist[i], bins=50, range=(0, 50))
ax.set_xlim(0, 50)

plt.show()

In [211]:
data[data[:, -1] == extra]

array([[288, 108,   1],
       [293, 109,   1],
       [281, 109,   1],
       [284, 108,   1],
       [284, 110,   1]])

In [107]:
plt.close('all')

In [399]:
data = label_nearest_spots(new_spots, max_dist=15, max_neighbors=5)

In [400]:
fig, ax = plt.subplots(1, 1, figsize=(10, 5), dpi=200)

im = ax.imshow(fixed_img)
fig.colorbar(im, ax=ax)
ax.scatter(data[:, 1], data[:, 0], c=data[:, 2], s=1, cmap='tab20')

plt.show()

In [129]:
fig, ax = plt.subplots(1, 1, figsize=(5, 5), dpi=200)

ax.scatter(manifold_pred[:, 0], manifold_pred[:, 1])

plt.show()

In [128]:
from sklearn import cluster, manifold

spots = peak_local_max(fixed_img, threshold_rel=0.05)

#test = cluster.AgglomerativeClustering(n_clusters=None, distance_threshold=10, linkage='single')

#test_manifold = manifold.LocallyLinearEmbedding(method='modified')
test_manifold = manifold.Isomap(n_neighbors=2)
test_cluster = cluster.AgglomerativeClustering(n_clusters=None, distance_threshold=1e-10, linkage='single')
manifold_pred = test_manifold.fit_transform(spots)
pred = test_cluster.fit_predict(manifold_pred)
print(len(np.unique(pred)))

fig, ax = plt.subplots(1, 1, figsize=(6, 5), dpi=200)

im = ax.imshow(fixed_img)
ax.scatter(spots[:, 1], spots[:, 0], c=pred, s=1, cmap='tab20')
fig.colorbar(im, ax=ax)

plt.show()

c:\Users\emusterma\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\manifold\_isomap.py:383: UserWarning: The number of connected components of the neighbors graph is 168 > 1. Completing the graph to fit Isomap might be slow. Increase the number of neighbors to avoid this issue.
  self._fit_transform(X)
c:\Users\emusterma\AppData\Local\Programs\Python\Python311\Lib\site-packages\scipy\sparse\_index.py:100: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_intXint(row, col, x.flat[0])
c:\Users\emusterma\AppData\Local\Programs\Python\Python311\Lib\site-packages\scipy\sparse\_index.py:100: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_intXint(row, col, x.flat[0])
c:\Users\emusterma\AppData\Local\Programs\Python\Python311\Lib\site-packages\scipy\sparse\_index.py:100: SparseEfficiencyWarning: Changing the sparsity 

2907


In [14]:
from pyFAI.blob_detection import BlobDetection

#blobs = BlobDetection(fixed_img, cur_sigma=0.25, init_sigma=0.01, dest_sigma=0.5, scale_per_octave=2, mask=None)
blobs = BlobDetection(fixed_img, init_sigma=0.01, dest_sigma=0.25)
blobs.process()

After refinement : 1334 keypoints
After refinement : 393 keypoints
After refinement : 2 keypoints


In [26]:
fig, ax = plt.subplots(1, 1, figsize=(5, 5), dpi=200)

im = ax.imshow(blobs.dogs[3])
fig.colorbar(im, ax=ax)

plt.show()

In [34]:
blobs.keypoints['x']

array([ 10.1489  , 507.1385  ,  37.883053, ...,  64.3305  ,  49.73627 ,
       385.9631  ], dtype=float32)

In [40]:
fig, ax = plt.subplots(1, 1, figsize=(6, 5), dpi=200)

im = ax.imshow(fixed_img)
ax.scatter(blobs.keypoints['x'], blobs.keypoints['y'], c='r', s=1)
fig.colorbar(im, ax=ax)

plt.show()

In [62]:
from pyFAI.gui.widgets.peak_picker import PeakPicker

ModuleNotFoundError: No module named 'pyFAI.gui.widgets.peak_picker'

In [70]:
peak_picker = pyFAI.gui.peak_picker.PeakPicker(proc_img)

In [463]:
blobs = pyFAI.blob_detection.BlobDetection(proc_img, scale_per_octave=3)

In [464]:
blobs.process()

After refinement : 0 keypoints
After refinement : 0 keypoints
After refinement : 0 keypoints
After refinement : 0 keypoints
After refinement : 0 keypoints
After refinement : 0 keypoints


In [137]:
blobs.dogs.shape

(5, 16, 24)

In [126]:
patch = img[y - (s_patch - 1) / 2:y + (s_patch - 1) / 2 + 1, x - (s_patch - 1) / 2:x + (s_patch - 1) / 2 + 1]

TypeError: slice indices must be integers or None or have an __index__ method

In [129]:
y - (s_patch - 1) / 2

4.048779010772705